In [3]:
import pandas as pd
import numpy as np

In [4]:
df = pd.read_csv('ab_browser_test.csv')
df.head()

userID     browser     slot  n_clicks  n_queries  n_nonclk_queries
0       1  Browser #2      exp        23         32                19
1       3  Browser #4      exp         3          4                 2
2       5  Browser #4      exp        29         35                16
3       6  Browser #4  control        12          6                 0
4       7  Browser #4      exp        54         68                30

Описание данных:
    
•userID: уникальный идентификатор пользователя
    
•browser: браузер, который использовал userID
    
•slot: в каком статусе пользователь участвовал в исследовании (exp = видел измененную страницу, 
                                                               control = видел неизменную страницу)
    
•n_clicks: количество кликов, которые пользоваль совершил за n_queries
    
•n_queries: количество запросов, который совершил userID, пользуясь браузером browser
    
•n_nonclk_queries: количество запросов пользователя, в которых им не было совершено ни одного клика


1) Основная метрика, на которой мы сосредоточимся в этой работе, — это количество пользовательских кликов на web-странице в зависимости от тестируемого изменения этой страницы. 

Посчитайте, насколько в группе exp больше пользовательских кликов по сравнению с группой control в процентах от числа кликов в контрольной группе.


In [5]:
df['slot'].value_counts() #выборки разбиты примерно поровну

control    284554
exp        281580
Name: slot, dtype: int64

In [6]:
exp_clic = df[df['slot']=='exp']['n_clicks'].sum()
control_clic = df[df['slot']=='control']['n_clicks'].sum()
print 'exp_clics:', exp_clic
print 'control_clics:', control_clic
print (exp_clic-control_clic)/float(control_clic)*100, '%'

exp_clics: 3261823
control_clics: 3210027
1.6135689824415809 %


### Вопрос 2

Давайте попробуем посмотреть более внимательно на разницу между двумя группами (control и exp) относительно количества пользовательских кликов.

Для этого постройте с помощью бутстрепа 95% доверительный интервал для средних значений и медиан количества кликов в каждой из двух групп. Отметьте все верные утверждения. 


In [7]:
import scipy
from statsmodels.stats.weightstats import *
from statsmodels.stats.proportion import proportion_confint

In [21]:
def get_bootstrap_samples(data, n_samples): #функция генерации n_samples выборок из data, методом bootstrap
    indices = np.random.randint(0, len(data), (n_samples, len(data)))
    samples = data[indices]
    return samples
def stat_intervals(stat, alpha): #функция генерации доверительного интервала для статисики
    boundaries = np.percentile(stat, [100 * alpha / 2., 100 * (1 - alpha / 2.)])
    return boundaries

Проверим гипотезу о равенстве медиан в control и exp группах

In [25]:
random_state = 0
df_exp_boot = map(np.median, get_bootstrap_samples(df[df.slot == 'exp'].n_clicks.values, 500)) #генерируем выборки и находим медианы
df_control_boot = map(np.median, get_bootstrap_samples(df[df.slot == 'control'].n_clicks.values, 500))

print 'exp_clic median: ', sum(df_exp_boot) / float(len(df_exp_boot)) #считаем среденее значение медианы в 1000 выборках 
print 'control_clic median: ', sum(df_control_boot) / float(len(df_control_boot))

delta_median_scores_clic = map(lambda x: x[0] - x[1], zip(df_exp_boot, df_control_boot)) # оценка разности медиан

print 'delta ', sum(delta_median_scores_clic) / float(len(delta_median_scores_clic)) #средняя разность

print "95% confidence interval for the difference between medians",  stat_intervals(delta_median_scores_clic, 0.05) #доверительный интервал

exp_clic median:  5.0
control_clic median:  4.0
delta  1.0
95% confidence interval for the difference between medians [1. 1.]


Доверительный интервал не содержит 0. Разница в медианах статистически значима.

Проверим гипотезу о равенстве средних в control и exp группах

In [26]:
random_state = 0
df_exp_boot = map(np.mean, get_bootstrap_samples(df[df.slot == 'exp'].n_clicks.values, 500)) #генерируем выборки и находим медианы
df_control_boot = map(np.mean, get_bootstrap_samples(df[df.slot == 'control'].n_clicks.values, 500))

print 'exp_clic mean: ', sum(df_exp_boot) / float(len(df_exp_boot)) #считаем среденее значение медианы в 1000 выборках 
print 'control_clic mean: ', sum(df_control_boot) / float(len(df_control_boot))

delta_mean_scores_clic = map(lambda x: x[0] - x[1], zip(df_exp_boot, df_control_boot)) # оценка разности медиан

print 'delta ', sum(delta_mean_scores_clic) / float(len(delta_mean_scores_clic)) #средняя разность

print "95% confidence interval for the difference between means",  stat_intervals(delta_mean_scores_clic, 0.05) #доверительный интервал

exp_clic mean:  11.584063058455843
control_clic mean:  11.279003289358071
delta  0.3050597690977731
95% confidence interval for the difference between means [0.20501837 0.42072196]


Доверительный интервал не содержит 0. Разница в средних статистически значима.

### Вопрос 3. 
Поскольку данных достаточно много (порядка полумиллиона уникальных пользователей), отличие в несколько процентов может быть не только практически значимым, но и значимым статистически. Последнее утверждение нуждается в дополнительной проверке. 

In [28]:
from plotly.offline import download_plotlyjs, init_notebook_mode, plot, iplot
import plotly.graph_objs as go
from plotly.subplots import make_subplots
init_notebook_mode(connected=True)

fig = make_subplots(rows=1, cols=2, specs=[[{"type": "bar"}, {"type": "bar"}]], subplot_titles=[])
fig.add_trace(go.Histogram(x=df[df['slot']=='control']['n_clicks'], name='control'), 1, 1)
fig.add_trace(go.Histogram(x=df[df['slot']=='exp']['n_clicks'], name='exp'), 1, 2)
fig.show()